In [ ]:
import numpy as np
import pandas as pd
import keras
from keras import regularizers, optimizers
from keras.layers import Input, Conv1D, Dense, Flatten, Activation, UpSampling1D, MaxPooling1D, ZeroPadding1D
from keras.callbacks import ModelCheckpoint, TensorBoard
from keras.models import Model, load_model
from keras.utils import to_categorical
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from sklearn.metrics import roc_auc_score


In [ ]:
df = pd.read_csv("creditcard.csv", sep=",", index_col=None)
print(df.shape)
df.head()

(59511, 31)


Time        V1        V2        V3        V4        V5        V6        V7  \
0     0 -1.359807 -0.072781  2.536347  1.378155 -0.338321  0.462388  0.239599   
1     0  1.191857  0.266151  0.166480  0.448154  0.060018 -0.082361 -0.078803   
2     1 -1.358354 -1.340163  1.773209  0.379780 -0.503198  1.800499  0.791461   
3     1 -0.966272 -0.185226  1.792993 -0.863291 -0.010309  1.247203  0.237609   
4     2 -1.158233  0.877737  1.548718  0.403034 -0.407193  0.095921  0.592941   

         V8        V9  ...       V21       V22       V23       V24       V25  \
0  0.098698  0.363787  ... -0.018307  0.277838 -0.110474  0.066928  0.128539   
1  0.085102 -0.255425  ... -0.225775 -0.638672  0.101288 -0.339846  0.167170   
2  0.247676 -1.514654  ...  0.247998  0.771679  0.909412 -0.689281 -0.327642   
3  0.377436 -1.387024  ... -0.108300  0.005274 -0.190321 -1.175575  0.647376   
4 -0.270533  0.817739  ... -0.009431  0.798278 -0.137458  0.141267 -0.206010   

        V26       V27       V28  Amount  Class  
0 -0.189115  0.133558 -0.021053  149.62    0.0  
1  0.125895 -0.008983  0.014724    2.69    0.0  
2 -0.139097 -0.055353 -0.059752  378.66    0.0  
3 -0.221929  0.062723  0.061458  123.50    0.0  
4  0.502292  0.219422  0.215153   69.99    0.0  

[5 rows x 31 columns]

In [ ]:
df.tail()

Time        V1        V2        V3        V4        V5        V6  \
51586  45023 -2.943382 -2.332451  2.568959  0.747114  2.083550 -1.319267   
51587  45024 -1.278283 -3.726046 -0.902718  2.796542 -1.750987  0.199763   
51588  45024 -0.852261  0.886192 -0.378032 -1.142044  1.880941  3.505875   
51589  45024 -0.447740  0.775759  1.586053  0.227702 -0.270962 -0.539013   
51590  45026  1.042380 -1.096464  0.234271 -0.615254 -1.243107 -0.714834   

             V7        V8        V9  ...       V21       V22       V23  \
51586 -1.837967  0.421285  0.347715  ... -0.013848 -0.091317 -0.268974   
51587  1.223412 -0.106145  0.793279  ...  0.664178 -0.592258 -1.141974   
51588 -0.403582  1.365218 -0.369193  ...  0.091829  0.066337 -0.055970   
51589  0.488655  0.071070  0.308739  ... -0.033903  0.202157 -0.180777   
51590 -0.433026 -0.084918 -0.946072  ...       NaN       NaN       NaN   

            V24       V25       V26       V27       V28   Amount  Class  
51586  0.069693  0.202920  0.356930 -0.006093  0.268288    26.24    0.0  
51587  0.322687  0.081328 -0.354449 -0.150956  0.269036  1233.16    0.0  
51588  1.027545 -0.327900  0.255778  0.132317  0.133329    28.98    0.0  
51589  0.424592 -0.172455  0.365861  0.353120  0.198239     3.99    0.0  
51590       NaN       NaN       NaN       NaN       NaN      NaN    NaN  

[5 rows x 31 columns]

In [ ]:
df['Amount'] = StandardScaler().fit_transform(df['Amount'].values.reshape(-1, 1))
df['Time'] = StandardScaler().fit_transform(df['Time'].values.reshape(-1, 1))
df.tail()

Time        V1        V2        V3        V4        V5        V6  \
59506  1.252750  0.846847 -0.740109  1.734920  0.973051 -0.908455  1.955373   
59507  1.252823 -0.293073  0.287754  1.076909 -1.498707  0.030389 -0.094332   
59508  1.252823 -2.728620  2.789470 -0.019110 -0.345316 -0.983749 -0.665490   
59509  1.252823 -0.118399  1.825136 -0.621394  0.294209  1.095673 -2.164019   
59510  1.252896 -2.101431  0.822359  0.342028 -0.592551  1.344203  4.774187   

             V7        V8        V9  ...       V21       V22       V23  \
59506 -1.282036  0.785884  1.530679  ...  0.108577  0.830381  0.111284   
59507  0.592840 -0.236917 -1.592913  ... -0.702190 -1.566421  0.092062   
59508 -0.452156  1.174699  0.050815  ... -0.080194 -0.098998  0.034646   
59509  1.102808 -1.244775 -0.734142  ...  0.595335 -0.750841 -0.418729   
59510  0.214765  1.215894  1.024100  ...       NaN       NaN       NaN   

            V24       V25       V26       V27       V28    Amount  Class  
59506 -0.338765 -0.038436  0.663828  0.107897  0.023937 -0.190358    0.0  
59507 -0.345236 -0.562907  0.566838 -0.462258 -0.231659 -0.256997    0.0  
59508 -0.090487  0.025606  0.152858 -0.341898 -0.263507 -0.345886    0.0  
59509  0.595806  1.411615 -0.561365  0.139271  0.280751 -0.349551    0.0  
59510       NaN       NaN       NaN       NaN       NaN       NaN    NaN  

[5 rows x 31 columns]

In [ ]:
fraud = df[df["Class"] == 1]
normal = df[df["Class"] == 0]

fraud.shape, normal.shape


((162, 31), (59348, 31))

In [ ]:

for f in range(0, 20):
    normal = normal.iloc[np.random.permutation(len(normal))]
    

data_set = pd.concat([normal[:10000], fraud])

x_train, x_test = train_test_split(data_set, test_size = 0.4, random_state = 42)

x_train = x_train.sort_values(by=['Time'])
x_test = x_test.sort_values(by=['Time'])

y_train = x_train["Class"]
y_test = x_test["Class"]

x_train.head(10)

Time        V1        V2        V3        V4        V5        V6  \
23  -2.321760  0.247491  0.277666  1.185471 -0.092603 -1.314394 -0.150116   
38  -2.320955  0.996370 -0.122589  0.546819  0.706580  0.134560  1.156995   
47  -2.320589  0.201686  0.497483  1.373913  0.571405 -0.630658 -0.539659   
76  -2.319491 -0.549626  0.418949  1.729833  0.203065 -0.187012  0.253878   
77  -2.319491  0.921544 -0.067084  0.077461  0.953638  0.067412  0.016152   
132 -2.317004 -1.864990  0.910874  1.724863 -1.748371  0.578943 -0.832531   
134 -2.317004 -1.897331  0.955626  0.052543  1.276656 -3.323084  3.229911   
135 -2.316930  1.119272 -0.669639  0.803807 -0.651693 -1.395666 -0.800698   
142 -2.316564  0.270725 -1.615317  1.054982  1.661510 -1.737687  0.065894   
147 -2.316345  0.607153 -0.957413  0.761505  1.590050 -1.177298  0.011232   

           V7        V8        V9  ...       V21       V22       V23  \
23  -0.946365 -1.617935  1.544071  ...  1.650180  0.200454 -0.185353   
38  -0.294561  0.407429  0.337863  ... -0.076302  0.108867  0.162231   
47  -0.076270 -0.917106  0.270008  ...  0.718961 -0.171877 -0.166205   
76   0.500894  0.251256 -0.227985  ...  0.115062  0.418529 -0.065133   
77   0.320452  0.038534 -0.391513  ... -0.333930 -1.299920  0.084311   
132  1.901440 -1.913986  2.112375  ... -0.318597  0.073323 -0.061693   
134  1.029631  1.515607 -0.059627  ...  0.128416  0.776078  0.477537   
135 -0.601605  0.014390  2.019905  ...  0.163687  0.546516 -0.176836   
142 -0.313977  0.089081  1.069842  ...  0.475338  0.496083 -0.482194   
147 -0.166991  0.152720  0.742860  ...  0.166237  0.100682 -0.317001   

          V24       V25       V26       V27       V28    Amount  Class  
23   0.423073  0.820591 -0.227632  0.336634  0.250475 -0.269029    0.0  
38  -0.575624  0.109795  0.373813  0.050552  0.005106 -0.277247    0.0  
47   0.776471  0.818460  0.442547  0.142757  0.219238 -0.316268    0.0  
76   0.264981  0.003958  0.395969  0.027182  0.043506 -0.131160    0.0  
77  -0.370398  0.155102 -0.834490  0.000909  0.035547  0.148427    0.0  
132  0.547204 -0.466798  0.408030 -2.377933 -1.255549 -0.324783    0.0  
134 -0.608981 -1.120892 -0.413851  0.061399 -0.187964  1.691007    0.0  
135  0.402556  0.563402 -0.534236  0.075047  0.042001 -0.104097    0.0  
142  0.418871  0.235961 -0.265185 -0.001063  0.120126  1.347484    0.0  
147  0.543778  0.484232 -0.330425 -0.001545  0.062098  0.641814    0.0  

[10 rows x 31 columns]

In [ ]:
print("Shapes:\nx_train:%s\ny_train:%s\n" % (x_train.shape, y_train.shape))
print("x_test:%s\ny_test:%s\n" % (x_test.shape, y_test.shape))



Shapes:
x_train:(6097, 31)
y_train:(6097,)

x_test:(4065, 31)
y_test:(4065,)



In [ ]:
x_train = np.array(x_train).reshape(x_train.shape[0], x_train.shape[1], 1)
x_test = np.array(x_test).reshape(x_test.shape[0], x_test.shape[1], 1)
input_shape = (x_train.shape[1], 1)

y_train = keras.utils.to_categorical(y_train, 2)
y_test = keras.utils.to_categorical(y_test, 2)

In [ ]:
print("Shapes:\nx_train:%s\ny_train:%s\n" % (x_train.shape, y_train.shape))
print("x_test:%s\ny_test:%s\n" % (x_test.shape, y_test.shape))
print("input_shape:{}\n".format(input_shape))


Shapes:
x_train:(6097, 31, 1)
y_train:(6097, 2)

x_test:(4065, 31, 1)
y_test:(4065, 2)

input_shape:(31, 1)



In [ ]:

input_layer = Input(shape=input_shape)

### ENCODING STAGE
# Pairs of causal 1D convolutional layers and pooling layers comprising the encoding stage
conv_1 = Conv1D(filters=input_shape[0], kernel_size=2, dilation_rate=1,
                padding='causal', strides=1,input_shape=input_shape,
                kernel_regularizer=regularizers.l2(0.01),
                activation='relu')(input_layer)

pool_1 = MaxPooling1D(pool_size=2, strides=2)(conv_1)

conv_2 = Conv1D(filters=int(input_shape[0] / 2), kernel_size=2,
                dilation_rate=1, padding='causal', strides=1,
                kernel_regularizer=regularizers.l2(0.01),
                activation='relu')(pool_1)

pool_2 = MaxPooling1D(pool_size=2, strides=3)(conv_2)

conv_3 = Conv1D(filters=int(input_shape[0] / 3), kernel_size=2, dilation_rate=1,
                padding='causal', strides=1,kernel_regularizer=regularizers.l2(0.01),
                activation='relu')(pool_2)


### OUTPUT OF ENCODING STAGE
encoder = Dense(int(input_shape[0] / 6), activation='relu')(conv_3)

### DECODING STAGE
# Pairs of upsampling and causal 1D convolutional layers comprising the decoding stage
upsample_1 = UpSampling1D(size=3)(encoder)

conv_4 = Conv1D(filters=int(input_shape[0]/3), kernel_size=2, dilation_rate=1,
                padding='causal',strides=1, kernel_regularizer=regularizers.l2(0.01),
                activation='relu')(upsample_1)

upsample_2 = UpSampling1D(size=2)(conv_4)

conv_5 = Conv1D(filters=int(input_shape[0]/2), kernel_size=2, dilation_rate=1,
                padding='causal', strides=1,kernel_regularizer=regularizers.l2(0.05),
                activation='relu')(upsample_2)

zero_pad_1 = ZeroPadding1D(padding=(0,1))(conv_5)

conv_6 = Conv1D(filters=int(input_shape[0]), kernel_size=2, dilation_rate=1,
                padding='causal', strides=1,kernel_regularizer=regularizers.l2(0.05),
                activation='relu')(zero_pad_1)


### Output of decoding stage flattened and passed through softmax to make predictions
flat = Flatten()(conv_6)

output_layer = Dense(2, activation='softmax')(flat)

TCN = Model(inputs=input_layer, outputs=output_layer)

In [ ]:
TCN.compile(loss=keras.losses.categorical_crossentropy,
              optimizer=optimizers.Adam(lr=0.002),
           metrics=["accuracy"])

checkpointer = ModelCheckpoint(filepath='best_weights.hdf5', verbose=1, save_best_only=True)

TCN.summary()

Model: "model_1"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_2 (InputLayer)        [(None, 31, 1)]           0         
                                                                 
 conv1d_6 (Conv1D)           (None, 31, 31)            93        
                                                                 
 max_pooling1d_2 (MaxPooling  (None, 15, 31)           0         
 1D)                                                             
                                                                 
 conv1d_7 (Conv1D)           (None, 15, 15)            945       
                                                                 
 max_pooling1d_3 (MaxPooling  (None, 5, 15)            0         
 1D)                                                             
                                                                 
 conv1d_8 (Conv1D)           (None, 5, 10)             310 

/usr/local/lib/python3.8/dist-packages/keras/optimizers/optimizer_v2/adam.py:117: UserWarning: The `lr` argument is deprecated, use `learning_rate` instead.
  super().__init__(name, **kwargs)


In [ ]:
TCN.fit(x_train, y_train,
          batch_size=128,
          epochs=25,
          verbose=1,
          validation_data=(x_test, y_test),
          callbacks = [checkpointer])


Epoch 1/25
47/48 [============================>.] - ETA: 0s - loss: 1.5385 - accuracy: 0.9727
Epoch 1: val_loss improved from inf to 0.82524, saving model to best_weights.hdf5
48/48 [==============================] - 2s 20ms/step - loss: 1.5290 - accuracy: 0.9729 - val_loss: 0.8252 - val_accuracy: 0.9852
Epoch 2/25
43/48 [=========================>....] - ETA: 0s - loss: 0.5671 - accuracy: 0.9862
Epoch 2: val_loss improved from 0.82524 to 0.33244, saving model to best_weights.hdf5
48/48 [==============================] - 1s 15ms/step - loss: 0.5451 - accuracy: 0.9870 - val_loss: 0.3324 - val_accuracy: 0.9938
Epoch 3/25
43/48 [=========================>....] - ETA: 0s - loss: 0.2397 - accuracy: 0.9933
Epoch 3: val_loss improved from 0.33244 to 0.16484, saving model to best_weights.hdf5
48/48 [==============================] - 1s 15ms/step - loss: 0.2347 - accuracy: 0.9923 - val_loss: 0.1648 - val_accuracy: 0.9943
Epoch 4/25
43/48 [=========================>....] - ETA: 0s - loss: 0.1311

In [ ]:

score = TCN.evaluate(x_test, y_test, verbose=0)
print('Test loss:', score[0])
print('Test accuracy:', score[1])

Test loss: 0.03800477460026741
Test accuracy: 0.9960639476776123


In [ ]:
from sklearn.metrics import roc_auc_score

preds = TCN.predict(x_test)
auc = roc_auc_score( np.round(preds), y_test)
print("AUC: {:.2%}".format (auc))

128/128 [==============================] - 0s 2ms/step
AUC: 93.23%


In [ ]:

predictions = TCN.predict(x_test)
predictions = predictions[:, ::2]  # take every 2nd value along time axis
mse = np.mean(np.power(x_test - predictions, 2), axis=(1,2))

128/128 [==============================] - 0s 3ms/step


ValueError: ignored

In [ ]:
predictions[0].shape

(30, 1)

In [ ]:
for f in range(0, len(x_test)):
    print(x_test[f], predictions[f])

[[-1.99605658]
 [ 1.1140086 ]
 [ 0.08554609]
 [ 0.49370249]
 [ 1.33575999]
 [-0.30018855]
 [-0.01075378]
 [-0.11876002]
 [ 0.1886167 ]
 [ 0.20568685]
 [ 0.08226226]
 [ 1.13355567]
 [ 0.626699  ]
 [-1.49278039]
 [ 0.52078789]
 [-0.6745926 ]
 [-0.52910824]
 [ 0.1582562 ]
 [-0.39875148]
 [-0.14570891]
 [-0.27383237]
 [-0.05323366]
 [-0.00476015]
 [-0.03147017]
 [ 0.19805372]
 [ 0.56500731]
 [-0.33771813]
 [ 0.0290574 ]
 [ 0.00445263]
 [-0.33543791]] [[1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]]
[[-1.99603552e+00]
 [-5.29912284e-01]
 [ 8.73891581e-01]
 [ 1.34724733e+00]
 [ 1.45456677e-01]
 [ 4.14208858e-01]
 [ 1.00223094e-01]
 [ 7.11206083e-01]
 [ 1.76065957e-01]
 [-2.86716935e-01]
 [-4.84687683e-01]
 [ 8.72489590e-01]
 [ 8.51635860e-01]
 [-5.71745303e-01]
 [ 1.00974273e-01]
 [-1.51977183e+00]
 [-2.84375978e-01]
 [-3.10523585e-01]
 [-4.04247869e-01]
 [-8.23

 [-0.3496711 ]] [[1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]]
[[-1.65285453]
 [-1.45293124]
 [-1.19553896]
 [ 2.0789652 ]
 [ 0.78831321]
 [-1.36913976]
 [ 1.26724142]
 [ 1.62862398]
 [-0.8991001 ]
 [ 1.83709291]
 [ 0.01860847]
 [ 2.13619002]
 [-2.09171488]
 [ 2.09210886]
 [ 0.36587268]
 [-0.1300233 ]
 [-0.35926207]
 [ 0.49609165]
 [ 0.74189703]
 [ 2.30080839]
 [ 0.05451938]
 [-0.45157666]
 [ 0.08950795]
 [-0.19022009]
 [ 0.11361994]
 [-0.53775396]
 [ 1.09530897]
 [-0.39342826]
 [-0.49098781]
 [ 1.6458137 ]] [[1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]]
[[-1.64683197]
 [-1.16034691]
 [ 0.27360458]
 [ 2.2465346 ]
 [ 0.40061343]
 [ 0.67046123]
 [-0.13695582]
 [ 0.13220413]
 [ 0.18103947]
 [ 0.71193398]
 [-0.98215207]
 [ 2.2

 [1.]]
[[-1.38979895]
 [ 1.41377505]
 [-0.76383805]
 [ 1.01535048]
 [-0.81894044]
 [-1.34435063]
 [-0.04752102]
 [-1.32416213]
 [ 0.07563981]
 [-0.15743828]
 [ 0.57680493]
 [-1.04337266]
 [-0.75107234]
 [ 0.82354797]
 [-0.73108658]
 [ 1.34498972]
 [ 1.93402805]
 [-0.37012802]
 [-0.39842883]
 [ 0.41596501]
 [ 0.14163864]
 [ 0.38261286]
 [ 1.09049652]
 [-0.18765694]
 [-0.4044479 ]
 [ 0.43620901]
 [ 0.00891699]
 [ 0.05888973]
 [ 0.02500904]
 [-0.31328851]] [[1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]]
[[-1.38977789]
 [ 1.25390039]
 [-0.08737129]
 [-0.76360872]
 [-0.04269786]
 [ 1.85315687]
 [ 3.5998954 ]
 [-0.80654228]
 [ 0.91737253]
 [ 0.18434061]
 [ 0.03708952]
 [-0.19755766]
 [ 0.03628032]
 [ 0.10808502]
 [ 0.26184299]
 [ 1.42538383]
 [ 0.71711038]
 [-1.09312257]
 [ 0.64540065]
 [-0.20003308]
 [ 0.00903509]
 [ 0.08195194]
 [ 0.1329199 ]
 [-0.12273929]
 

[[-1.26385151]
 [-0.84194623]
 [ 1.1429455 ]
 [ 1.79008545]
 [ 2.48253574]
 [ 0.79008182]
 [ 2.99626758]
 [-0.017301  ]
 [ 0.55561308]
 [-0.18224124]
 [ 1.26125377]
 [-0.6317122 ]
 [-0.17698637]
 [ 0.28356547]
 [-0.66049389]
 [ 1.46813194]
 [-1.45501355]
 [ 1.02113218]
 [-1.51931068]
 [-0.36895716]
 [ 0.29361984]
 [ 0.14629839]
 [ 1.10142516]
 [-0.19873198]
 [-1.76576134]
 [-0.48580264]
 [ 0.47767342]
 [ 0.19464667]
 [ 0.03144303]
 [-0.23824443]] [[1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]]
[[-1.26353564e+00]
 [-6.03670496e-01]
 [ 1.05508131e+00]
 [ 7.57501212e-01]
 [-1.25712405e-01]
 [-1.06639236e-01]
 [-5.64457467e-01]
 [ 2.70281293e-01]
 [ 4.83020267e-01]
 [-7.37319622e-01]
 [-4.45082890e-01]
 [ 4.81582376e-01]
 [-1.42319073e-01]
 [-1.39164877e+00]
 [ 1.02687091e+00]
 [ 8.77840522e-02]
 [ 4.81954321e-01]
 [-4.77630782e-01]
 [ 6.69212440e-01]
 [ 3.77

 [1.]]
[[-1.16348944]
 [-2.86909239]
 [ 3.52678788]
 [-3.12392739]
 [ 0.3697753 ]
 [-0.78795707]
 [-0.22304554]
 [-1.29540345]
 [ 2.57259211]
 [-0.82977723]
 [ 0.55934835]
 [-1.0368183 ]
 [ 1.45992013]
 [ 1.2505203 ]
 [ 1.99353476]
 [-0.14730968]
 [ 0.73402826]
 [-0.09724767]
 [ 0.99951378]
 [ 1.13853909]
 [ 0.14369121]
 [ 0.18574973]
 [ 0.28519578]
 [ 0.16136101]
 [-1.38974726]
 [-0.08696193]
 [-0.29081206]
 [ 0.21239667]
 [ 0.1300975 ]
 [-0.33887626]] [[1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]]
[[-1.16315252]
 [-0.75284457]
 [ 1.04590119]
 [ 0.89010695]
 [ 0.93537181]
 [ 0.14018581]
 [-0.43349438]
 [ 0.32301192]
 [ 0.39353622]
 [-0.85827712]
 [-0.49518166]
 [-0.42501468]
 [ 0.23690162]
 [ 0.28280717]
 [ 0.66186216]
 [ 1.21111735]
 [-0.5025185 ]
 [ 0.24879027]
 [-0.31360653]
 [ 0.06349112]
 [-0.04675731]
 [ 0.25548019]
 [ 0.60905592]
 [-0.06380158]
 

...

 [-0.09143471]] [[1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]]
[[ 1.04079084]
 [ 1.9571696 ]
 [-0.37891874]
 [-1.5353829 ]
 [ 0.92151729]
 [-0.2665261 ]
 [-0.44563401]
 [-0.57368362]
 [ 0.00632443]
 [-0.20369219]
 [ 0.11128201]
 [-0.75477042]
 [-0.98038629]
 [-0.846364  ]
 [-2.04558872]
 [ 0.56700858]
 [-0.61816697]
 [ 1.42947119]
 [ 2.36615968]
 [-1.63340023]
 [-0.53031836]
 [-0.41833468]
 [-0.75415882]
 [ 0.22751016]
 [ 0.38647934]
 [-0.21268287]
 [-0.70062993]
 [ 0.07468082]
 [ 0.03148602]
 [-0.09335379]] [[1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]]
[[ 1.04156998]
 [ 1.83096188]
 [-0.72177635]
 [-0.78981841]
 [ 0.09354063]
 [ 0.50873207]
 [ 2.31967812]
 [-1.10001735]
 [ 0.77748266]
 [ 1.10454466]
 [ 0.04130186]
 [ 0.6

 [-0.34607282]] [[1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]]
[[ 1.14014212]
 [ 2.0058379 ]
 [ 0.03599728]
 [-1.98195077]
 [ 0.47516469]
 [ 0.4683173 ]
 [-1.49321198]
 [ 0.87091198]
 [-0.59635674]
 [ 0.24292017]
 [-0.05523553]
 [-0.65630355]
 [ 0.81268803]
 [ 0.6085107 ]
 [ 0.51278336]
 [-0.24485058]
 [-0.98458256]
 [-0.08914514]
 [-0.75271609]
 [ 0.06758558]
 [-0.13489623]
 [ 0.17516548]
 [ 0.68727462]
 [-0.12085573]
 [ 0.06193733]
 [ 0.55558977]
 [-0.07295627]
 [-0.05295954]
 [-0.06516901]
 [-0.15332508]] [[1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]]
[[ 1.1406054 ]
 [-1.79026359]
 [-0.78510338]
 [-0.22609204]
 [-2.4130234 ]
 [ 0.62262743]
 [ 0.80326239]
 [ 0.76290342]
 [ 0.68663746]
 [-2.01468116]
 [-0.65139627]
 [ 0.5

 [-0.01579092]] [[1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]]
[[ 1.25535002]
 [-1.62128388]
 [ 0.2699038 ]
 [-0.53928397]
 [ 0.16608055]
 [ 1.04728765]
 [-0.44572101]
 [-0.49252318]
 [ 0.72515684]
 [-0.36538439]
 [-0.8570185 ]
 [-1.6221883 ]
 [ 0.84349271]
 [ 1.58409914]
 [ 0.55133777]
 [ 0.55045209]
 [-0.2994486 ]
 [-0.01266298]
 [ 0.11004925]
 [ 1.1901634 ]
 [-0.18991046]
 [ 0.16782581]
 [ 0.33882902]
 [-0.50684612]
 [ 0.1237634 ]
 [-0.41714402]
 [-0.24909427]
 [ 0.04724026]
 [-0.2441844 ]
 [-0.32880109]] [[1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]]
[[ 1.25625551]
 [ 2.0738624 ]
 [ 0.18296969]
 [-1.68247116]
 [ 0.42194524]
 [ 0.42714064]
 [-0.89280473]
 [ 0.20633843]
 [-0.25587479]
 [ 0.44564383]
 [-0.38695522]
 [-0.4

 [1.]]
[[ 1.38199238]
 [ 2.09594822]
 [-0.82340981]
 [-1.55248202]
 [-0.76928384]
 [-0.10356232]
 [-0.11597701]
 [-0.41154597]
 [-0.11996017]
 [-0.83981471]
 [ 1.09216153]
 [ 0.26792108]
 [ 0.47981181]
 [ 0.73543734]
 [ 0.30929353]
 [-0.07587803]
 [-0.95115929]
 [-0.77844307]
 [ 1.7522368 ]
 [-0.46611838]
 [-0.42039339]
 [-0.19289219]
 [-0.15621518]
 [ 0.10166395]
 [ 0.1151346 ]
 [-0.129079  ]
 [ 0.66182065]
 [-0.07311243]
 [-0.0602557 ]
 [-0.12381921]] [[1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]]
[[ 1.38348749]
 [ 2.0885952 ]
 [-0.87407548]
 [-1.25347704]
 [-0.80801837]
 [-0.70773878]
 [-1.3378222 ]
 [-0.21293069]
 [-0.39042867]
 [-0.46240672]
 [ 0.78163952]
 [-0.67670009]
 [-0.5851975 ]
 [-0.06144147]
 [ 0.05211047]
 [ 0.10412809]
 [ 0.91591485]
 [ 0.23832744]
 [-1.78233237]
 [ 0.75187704]
 [ 0.07797711]
 [-0.02533025]
 [-0.25785507]
 [ 0.23443789]
 

 [1.]]
[[ 1.47923787]
 [ 0.02258733]
 [ 0.79831682]
 [ 0.1472458 ]
 [-0.80278847]
 [ 0.69279693]
 [-0.49053293]
 [ 0.88006729]
 [-0.00751827]
 [-0.27483476]
 [-0.24814457]
 [ 0.4624285 ]
 [ 0.70501892]
 [-0.02744676]
 [ 0.29422248]
 [-1.02523693]
 [ 0.1615138 ]
 [-0.74681593]
 [-0.2100848 ]
 [ 0.28455472]
 [-0.02512004]
 [-0.23018451]
 [-0.51019084]
 [ 0.01167965]
 [-0.47334048]
 [-0.48237238]
 [ 0.15080186]
 [ 0.246355  ]
 [ 0.0824991 ]
 [-0.34607282]] [[1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]
 [1.]]
[[ 1.47936421]
 [ 1.8698821 ]
 [-0.62719866]
 [-0.30821114]
 [ 0.57513756]
 [-0.90256796]
 [-0.52950058]
 [-0.59619857]
 [-0.01923452]
 [ 1.56411927]
 [-0.17440596]
 [-1.05627592]
 [ 0.16699062]
 [-0.49290153]
 [-0.06595678]
 [ 0.59449085]
 [ 0.03779371]
 [-0.40498263]
 [ 0.2498204 ]
 [-0.34670449]
 [-0.16568942]
 [ 0.27838379]
 [ 0.93634254]
 [ 0.05257895]
 

In [ ]:

predictions = TCN.predict(x_test)

mse = np.mean(np.power(x_test - predictions, 2), axis=1)
error_df = pd.DataFrame({'reconstruction_error': mse,
                        'true_class': y_test}, index=[0])

error_df.describe()

Exception: Data must be 1-dimensional